In [1]:
import sys 
sys.path.append("../..")
sys.path.append("..")

from importlib import reload
from tqdm import tqdm

import joseph
from joseph.analysis import *
from joseph.visualisation import *
from joseph.utils import *
from joseph.data import *


reload(joseph.analysis)
reload(joseph.visualisation)
reload(joseph.utils)
reload(joseph.data)

from joseph.analysis import *
from joseph.visualisation import *
from joseph.utils import *
from joseph.data import *

# turn torch grad tracking off
torch.set_grad_enabled(False)

import webbrowser
from IPython.core.display import display, HTML

path_to_html = "../week_8_jan/gpt2_small_features_layer_5"
def render_feature_dashboard(feature_id):
    
    path = f"{path_to_html}/data_{feature_id:04}.html"
    
    print(f"Feature {feature_id}")
    if os.path.exists(path):
        # with open(path, "r") as f:
        #     html = f.read()
        #     display(HTML(html))
        webbrowser.open_new_tab("file://" + os.path.abspath(path))
    else:
        print("No HTML file found")
    

In [105]:
path_to_all_layer_saes = "../GPT2-small-SAEs/" 

log_sparsity_files = os.listdir(path_to_all_layer_saes)
# print(log_sparsity_files)
model_files = [f for f in log_sparsity_files if "log" not in f]
model_files = sorted(model_files, key=lambda x: int(x.split(".")[1]))
display(model_files)

log_sparsity_files = [f for f in log_sparsity_files if "log_feature_sparsity" in f]
log_sparsity_files = sorted(log_sparsity_files, key=lambda x: int(x.split(".")[1]))
log_sparsity_files

['final_sparse_autoencoder_gpt2-small_blocks.0.hook_resid_pre_24576.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.1.hook_resid_pre_24576.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.2.hook_resid_pre_24576.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.3.hook_resid_pre_24576.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.4.hook_resid_pre_24576.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.5.hook_resid_pre_24576.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.6.hook_resid_pre_24576.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.7.hook_resid_pre_24576.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.8.hook_resid_pre_24576.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.9.hook_resid_pre_24576.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.10.hook_resid_pre_24576.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.11.hook_resid_pre_24576.pt']

['final_sparse_autoencoder_gpt2-small_blocks.0.hook_resid_pre_24576_log_feature_sparsity.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.1.hook_resid_pre_24576_log_feature_sparsity.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.2.hook_resid_pre_24576_log_feature_sparsity.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.3.hook_resid_pre_24576_log_feature_sparsity.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.4.hook_resid_pre_24576_log_feature_sparsity.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.5.hook_resid_pre_24576_log_feature_sparsity.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.6.hook_resid_pre_24576_log_feature_sparsity.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.7.hook_resid_pre_24576_log_feature_sparsity.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.8.hook_resid_pre_24576_log_feature_sparsity.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.9.hook_resid_pre_24576_log_feature_sparsity.pt',
 'final_sparse_autoencoder_gpt2-small_blocks.10.hook_resid_p

In [106]:
import plotly.graph_objects as go
log_feature_sparsities = [
    torch.load(os.path.join(path_to_all_layer_saes, f))
    for f in log_sparsity_files
]
log_feature_sparsities = torch.stack(log_feature_sparsities)

tmp = pd.DataFrame(log_feature_sparsities.numpy(), columns=[f"feature_{i}" for i in range(log_feature_sparsities.shape[1])], index = [f"Layer {i}" for i in range(log_feature_sparsities.shape[0])])
fig = px.histogram(
    tmp.T, 
    facet_col="variable", 
    facet_col_wrap=4, 
    title="Feature Sparsity",
    # make it frequency
    histnorm="percent",
    nbins = 180,
    height=800,
    width = 1500,
    range_x=[-7, -1],
    range_y=[0, 18],
    color_discrete_sequence=["#a0a8ac","#cce4ff", "#c0d5ff", "#B6BFFF", 
                             "#BA96FE", "#D381FB", "#D381FB", "#B26CD4", 
                             "#8A4DAD", "#663785", "#44235C", "#1E0E2A"],
    template="none",
)

fig.update_layout(
    title="Log10 Feature Sparsity Histograms (24,576 Features)",
    showlegend=False,
    font=dict(
        size=18,
    )
)
# remove "variable = " from the facet titles
fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))

# remove "value" from the axis titles
fig.update_xaxes(title_text="")
fig.update_yaxes(title_text="")


fig.show()

In [102]:
import plotly.graph_objects as go
log_feature_sparsities = [
    torch.load(os.path.join(path_to_all_layer_saes, f))
    for f in log_sparsity_files
]
log_feature_sparsities = torch.stack(log_feature_sparsities)

tmp = pd.DataFrame(log_feature_sparsities.numpy(), columns=[f"feature_{i}" for i in range(log_feature_sparsities.shape[1])], index = [f"Layer {i}" for i in range(log_feature_sparsities.shape[0])])
fig = px.histogram(
    tmp,
    animation_frame=tmp.index, 
    # facet_col="variable", 
    # facet_col_wrap=4, 
    title="Feature Sparsity",
    # make it frequency
    histnorm="percent",
    nbins = 180,
    height=800,
    width = 1500,
    range_x=[-7, -1],
    range_y=[0, 18],
    color_discrete_sequence=["#a0a8ac","#cce4ff", "#c0d5ff", "#B6BFFF", 
                             "#BA96FE", "#D381FB", "#D381FB", "#B26CD4", 
                             "#8A4DAD", "#663785", "#44235C", "#1E0E2A"],
    template="none",
)

fig.update_layout(
    title="Log10 Feature Sparsity",
    showlegend=False,
    font=dict(
        size=18,
    )
)
# # remove "variable = " from the facet titles
# fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))

# # remove "value" from the axis titles
# fig.update_xaxes(title_text="")
# fig.update_yaxes(title_text="")


fig.show()

KeyboardInterrupt: 